In [17]:
# Initial imports
import pandas as pd
import hvplot.pandas
from path import Path
import plotly.express as px
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
import numpy as np

In [18]:
# Read data into a DataFrame
file_to_load=pd.read_csv('merged_data.csv')
data_df = pd.DataFrame(file_to_load)
data_df.head(10)

Unnamed: 0  date    price  bedrooms  bathrooms  sqft_living  sqft_lot  \
0           0  2014   221900         3       1.00         1180      5650   
1           1  2014   538000         3       2.25         2570      7242   
2           2  2015   180000         2       1.00          770     10000   
3           3  2014   604000         4       3.00         1960      5000   
4           4  2015   510000         3       2.00         1680      8080   
5           5  2014  1230000         4       4.50         5420    101930   
6           6  2014   257500         3       2.25         1715      6819   
7           7  2015   291850         3       1.50         1060      9711   
8           8  2015   229500         3       1.00         1780      7470   
9           9  2015   323000         3       2.50         1890      6560   

   floors  waterfront  view  condition  grade  yr_built  yr_renovated  \
0     1.0           0     0          3      7      1955             0   
1     2.0           0     0          3      7      1951          1991   
2     1.0           0     0          3      6      1933             0   
3     1.0           0     0          5      7      1965             0   
4     1.0           0     0          3      8      1987             0   
5     1.0           0     0          3     11      2001             0   
6     2.0           0     0          3      7      1995             0   
7     1.0           0     0          3      7      1963             0   
8     1.0           0     0          3      7      1960             0   
9     2.0           0     0          3      7      2003             0   

   zipcode  house_age  city_rank  
0    98178         59       10.0  
1    98125         63       10.0  
2    98028         82       14.0  
3    98136         49       10.0  
4    98074         28        4.0  
5    98053         13        5.0  
6    98003         19       24.0  
7    98198         52       10.0  
8    98146         55       10.0  
9    98038         12       20.0

In [22]:
# Initialize the K-Means model.
model = KMeans(n_clusters=5, random_state=5)
model

# Fit the model
model.fit(data_df)

KMeans(n_clusters=5, random_state=5)

In [23]:
# Create a new DataFrame including predicted clusters and house features.
clustered2_df = data_df

#  Add a new column, "Clusters" to the clustered_df DataFrame that holds the predictions.
clustered2_df['Cluster'] = model.labels_

# Filter out outliers
clustered2_df = clustered2_df[(clustered2_df['price'] < 4000000) & (clustered2_df['bedrooms'] < 30)] 

# Print the shape of the clustered_df
print(clustered2_df.shape)
clustered2_df.head(10)

(21423, 18)


Unnamed: 0  date    price  bedrooms  bathrooms  sqft_living  sqft_lot  \
0           0  2014   221900         3       1.00         1180      5650   
1           1  2014   538000         3       2.25         2570      7242   
2           2  2015   180000         2       1.00          770     10000   
3           3  2014   604000         4       3.00         1960      5000   
4           4  2015   510000         3       2.00         1680      8080   
5           5  2014  1230000         4       4.50         5420    101930   
6           6  2014   257500         3       2.25         1715      6819   
7           7  2015   291850         3       1.50         1060      9711   
8           8  2015   229500         3       1.00         1780      7470   
9           9  2015   323000         3       2.50         1890      6560   

   floors  waterfront  view  condition  grade  yr_built  yr_renovated  \
0     1.0           0     0          3      7      1955             0   
1     2.0           0     0          3      7      1951          1991   
2     1.0           0     0          3      6      1933             0   
3     1.0           0     0          5      7      1965             0   
4     1.0           0     0          3      8      1987             0   
5     1.0           0     0          3     11      2001             0   
6     2.0           0     0          3      7      1995             0   
7     1.0           0     0          3      7      1963             0   
8     1.0           0     0          3      7      1960             0   
9     2.0           0     0          3      7      2003             0   

   zipcode  house_age  city_rank  Cluster  
0    98178         59       10.0        3  
1    98125         63       10.0        0  
2    98028         82       14.0        3  
3    98136         49       10.0        0  
4    98074         28        4.0        0  
5    98053         13        5.0        2  
6    98003         19       24.0        3  
7    98198         52       10.0        3  
8    98146         55       10.0        3  
9    98038         12       20.0        3

In [25]:
# Creating a 3D-Scatter with the PCA data and the clusters
fig = px.scatter_3d(
    clustered2_df,
    x="house_age",
    y="price",
    z="city_rank",
    custom_data=['bedrooms', 'sqft_living', 'bathrooms', 'floors', 'city_rank', 'Cluster'],
    color="Cluster",
    symbol="Cluster",
    width=800,
    height=800
)
fig.update_traces(hovertemplate='Cluster: %{customdata[5]} <br>Price: $%{y:,.2f} <br>House Age: %{x} years <br>Bedrooms: %{customdata[0]} <br>Square Feet: %{customdata[1]:,f} <br>Bathrooms: %{customdata[2]} <br>Floors: %{customdata[3]} <br>City Rank: %{customdata[4]}')
fig.update_layout(title='3D Clustering of House Features', legend=dict(x=0, y=1), margin=dict(l=0, r=0, b=0, t=0), scene=dict(xaxis_title="Age of House", yaxis_title="Price of House", zaxis_title="City Rank"))
fig.update_layout(
    title={
        'y':0.98,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})
fig.show()

In [136]:
# Write 3D-Scatter to an HTML file
fig2.write_html('../chart.html',
                full_html=False,
                include_plotlyjs='cdn')